# Voting

In [1]:
# Importing the libraries
import numpy as np
import pandas as pd
import sklearn
import matplotlib.pyplot as plt
import sys
import numpy
numpy.set_printoptions(threshold=sys.maxsize)

# Importing the dataset
dataset = pd.read_csv('CVD dataset8.csv')
data=dataset.iloc[:, :].values
X = dataset.iloc[:, :-1].values
y = dataset.iloc[:, 8].values
# X = dataset.iloc[:, [ 0, 1, 2, 5, 10, 11, 13, 15]].values

rows = len(data)    # 3 rows in your example
cols = len(data[0])
print(rows)
print(cols)

560
9


In [2]:
dataNoCvd = data[~(data[:,8] > 0.0)]
dataCvd = data[~(data[:,8] < 1.0)]
rowsNoCvd = len(dataNoCvd)    
rowsCvd = len(dataCvd)
print(rowsNoCvd)
print(rowsCvd)
# print(dataNoCvd)
# print(dataCvd)

519
41


In [3]:
def find_NoCvd_limitsArray(i,DownNoCvd, UpNoCvd, fold_NoCvd_total, fold_NoCvd_residue):
    if i>0 :
        DownNoCvd = UpNoCvd
        UpNoCvd= fold_NoCvd_total+UpNoCvd
    if i < fold_NoCvd_residue :
        UpNoCvd+= 1
#     print("NoCvd limits, Down :",DownNoCvd,"Up ",UpNoCvd)
    return   DownNoCvd, UpNoCvd   
 
def find_Cvd_limitsArray(i,DownCvd, UpCvd, fold_Cvd_total, fold_Cvd_residue,cv):
    if i>0 :
        DownCvd = UpCvd
        UpCvd= fold_Cvd_total+UpCvd
    if i >= cv - fold_Cvd_residue :
         UpCvd+= 1     
#     print("Cvd limits, Down :",DownCvd,"Up ",UpCvd)
    return   DownCvd, UpCvd  

def find_testSubset(DownNoCvd,UpNoCvd,DownCvd,UpCvd):
    temp1=dataNoCvd[DownNoCvd:UpNoCvd,:]
    temp2=dataCvd[DownCvd:UpCvd,:]
    temp3=np.concatenate((temp1, temp2))
#     print(len(temp1),"  ",len(temp2),"  ",len(temp3))
    return temp1, temp2, temp3

def find_trainSubset(DownNoCvd,UpNoCvd,DownCvd,UpCvd):
    temp1 = np.delete(dataNoCvd, slice(DownNoCvd, UpNoCvd), axis=0)
    temp2 = np.delete(dataCvd, slice(DownCvd, UpCvd), axis=0)
    temp3 = np.concatenate((temp1, temp2))
#     print(len(temp1),"  ",len(temp2),"  ",len(temp3))
    return temp1, temp2, temp3

In [4]:
def create_train_test_sets(cv,dataNoCvd,dataCvd):
    test_total = []
    train_total = []
    train_total_Cvd = []
    train_total_NoCvd = []
    
    rowsNoCvd = len(dataNoCvd)    
    rowsCvd = len(dataCvd)

    fold_Cvd_total = rowsCvd//cv
    fold_Cvd_residue= rowsCvd%cv
    print("fold_Cvd_total  :",fold_Cvd_total," fold_Cvd_residue  :",fold_Cvd_residue)

    fold_NoCvd_total = rowsNoCvd//cv
    fold_NoCvd_residue= rowsNoCvd%cv
    print("fold_NoCvd_total:",fold_NoCvd_total,"fold_NoCvd_residue:",fold_NoCvd_residue)

    DownNoCvd=0
    DownCvd=0
    UpNoCvd = fold_NoCvd_total
    UpCvd = fold_Cvd_total

    for i in range(cv):
        X_test = []
        y_test = []
        X_train = []
        y_train = []
#         print("============",i,"==============")
        DownNoCvd, UpNoCvd = find_NoCvd_limitsArray(i, DownNoCvd, UpNoCvd, fold_NoCvd_total, fold_NoCvd_residue)
        DownCvd, UpCvd = find_Cvd_limitsArray(i, DownCvd, UpCvd, fold_Cvd_total, fold_Cvd_residue,cv)

        testSubset_NoCvd ,testSubset_Cvd ,testSubset_total = find_testSubset(DownNoCvd,UpNoCvd,DownCvd,UpCvd)
        trainSubset_NoCvd ,trainSubset_Cvd ,trainSubset_total = find_trainSubset(DownNoCvd,UpNoCvd,DownCvd,UpCvd)
     
    #creating X_train, y_train, X_test, y_test
        X_test.append(np.delete(testSubset_total, 8, axis=1))
        y_test_temp = np.delete(testSubset_total, slice(0, 8), axis=1)
        y_test.append(np.reshape(y_test_temp, len(y_test_temp)))
        X_test_temp = np.array(X_test)
        X_test = X_test_temp[0]
        y_test_temp = np.array(y_test)
        y_test = y_test_temp[0]
    
        X_train.append(np.delete(trainSubset_total, 8, axis=1))
        y_train_temp = np.delete(trainSubset_total, slice(0, 8), axis=1)
        y_train.append(np.reshape(y_train_temp, len(y_train_temp)))
        X_train_temp = np.array(X_train)
        X_train = X_train_temp[0]
        y_train_temp = np.array(y_train)
        y_train = y_train_temp[0]
        
    #add every subset in a list so we can handle thm later 
        test_total.append([X_test,y_test])
        train_total.append([X_train,y_train]) 
        train_total_NoCvd.append(trainSubset_NoCvd)
        train_total_Cvd.append(trainSubset_Cvd)
    return train_total, test_total, train_total_NoCvd, train_total_Cvd

In [5]:
train_total, test_total, train_total_NoCvd, train_total_Cvd = create_train_test_sets(10,dataNoCvd,dataCvd)

fold_Cvd_total  : 4  fold_Cvd_residue  : 1
fold_NoCvd_total: 51 fold_NoCvd_residue: 9


In [6]:
# Chech ratio in each train and test set
def find_ratio(index_list):
    one = 0
    lenght=len(index_list[0])
    for i in range(lenght):
#         print(index_list[1])
        if index_list[1][i] == 1.0 :
            one+= 1
    ratio = one/lenght
    return ratio

for i in range(10):
    print(len(train_total[i][0]))
    ratio = find_ratio(train_total[i])
    print("ratio in train set:", ratio)
    ratio = find_ratio(test_total[i])
    print("ratio in test set:", ratio)

504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07142857142857142
ratio in test set: 0.08928571428571429


In [7]:
from xgboost import XGBClassifier


def my_fit(ratio,dataNoCvd,dataCvd,params):   
    Subarray=[]
    models = []
    # yarray
    
    rowsNoCvd = len(dataNoCvd)    
    rowsCvd = len(dataCvd)
#     print("Size of NoCvd cases in train set:",rowsNoCvd)
#     print("Size of Cvd cases in train set  :",rowsCvd)


    numOfSubsamples = rowsNoCvd//(rowsCvd*ratio)
    numOfSubsamples= int(numOfSubsamples)
    SubNoCvd = rowsNoCvd//numOfSubsamples
    residue = rowsNoCvd- SubNoCvd*numOfSubsamples


    Up = 0


    for i in range(numOfSubsamples):
        
        classifier = XGBClassifier(base_score=0.5, booster='gbtree', colsample_bylevel=params[5],
                  colsample_bynode=1, colsample_bytree=1, gamma=params[4],
                  learning_rate=params[0], max_delta_step=0, max_depth=params[1],
                  min_child_weight=params[3], missing=None, n_estimators=params[2], n_jobs=1,
                  nthread=None, objective='binary:logistic', random_state=0,
                  reg_alpha=0, reg_lambda=params[6], scale_pos_weight=params[7], seed=None,
                  silent=None, subsample=1.0, verbosity=1)
    #     print(i)
    #Creating the training set for each model
        Down = Up
        Up= Up + SubNoCvd
        if i < residue :
            Up+= 1
        
#         print(Down)
#         print(Up)
        
        Sub1=dataNoCvd[Down:Up,:]
        Sub2=np.concatenate((Sub1, dataCvd))
        Subarray.append(Sub2)
        
    #Dividing to X and y of the previous traing set    
        X=np.delete(Subarray[i], 8, axis=1)
        y=np.delete(Subarray[i], slice(0, 8), axis=1)
        y=np.reshape(y, len(y))
        
        classifier.fit( X, y)
        models.append(classifier)
    return models     

In [8]:

def voting(models,X):
    y_pred = []
    y_pred_models = []

    models_size = len(models)
    X_size = len(X)
            
    for i in range(models_size):
        y_pred_models.append(models[i].predict(X))
        
    for j in range(X_size):
        case = 0
        for i in range(models_size):
            if y_pred_models[i][j] == 1.0:
                case+=1
        if case >  models_size/2 :
            y_pred.append(1.) 
        else:
            y_pred.append(0.) 
            
    return y_pred        
     

In [9]:
# https://towardsdatascience.com/train-test-split-and-cross-validation-in-python-80b61beca4b6

from sklearn.metrics import  confusion_matrix,roc_curve, roc_auc_score, accuracy_score
from imxgboost.imbalance_xgb import imbalance_xgboost as imb_xgb
from sklearn.model_selection import StratifiedKFold # import KFold
from sklearn import metrics

def my_cross_val( cv, train_total, test_total, train_total_NoCvd, train_total_Cvd,params):
    accuracy = []
    specificity = []
    sensitivity = []
    auc = []
    
    # print(X)
    for i in range(cv):
#         X_train = train_total[i][0]
#         y_train = train_total[i][1]
        X_test = test_total[i][0]
        y_test = test_total[i][1]
        


        models = my_fit( 2, train_total_NoCvd[i], train_total_Cvd[i],params)


        y_pred = voting(models,X_test)

        cm = confusion_matrix(y_test, y_pred)
    #     print(cm)

        total1=sum(sum(cm))
        #####from confusion matrix calculate accuracy
        accuracy1=(cm[0,0]+cm[1,1])/total1
    #   print ('Accuracy : ', accuracy1)

        specificity1 = cm[0,0]/(cm[0,0]+cm[0,1])
    #   print('Specificity : ', specificity1 )

        sensitivity1 = cm[1,1]/(cm[1,0]+cm[1,1])
    #   print('Sensitivity : ', sensitivity1)
        
#         y = np.array(y_test)
#         pred = np.array(y_pred)
#         fpr, tpr, thresholds = metrics.roc_curve(y, pred, pos_label=2)
#         auc1 = metrics.auc(fpr, tpr)
        
        auc1 = roc_auc_score(y_test, y_pred)

    
        accuracy.append(accuracy1)
        specificity.append(specificity1)
        sensitivity.append(sensitivity1) 
        auc.append(auc1)
    return accuracy, specificity, sensitivity, auc

In [10]:
# https://www.analyticsvidhya.com/blog/2016/03/complete-guide-parameter-tuning-xgboost-with-codes-python/        
params = {
                    "learning_rate"    :[ 0.1],  #0.01-0.2 Makes the model more robust by shrinking the weights on each step
                    "max_depth"        :[4],  #3-10 control over-fitting as higher depth will allow model to learn relations very specific to a particular sample
                    "n_estimators"     :[200],
                     "subsample"       :[1.0],         #0.5-1 small values might lead to under-fitting
                    "gamma"            :[0],            #Makes the algorithm conservative --> No overfitting
                    "colsample_bytree" :[0.5], #0.5-1
                     "reg_lambda"      :[1.5], #  it should be explored to reduce overfitting.
                    "scale_pos_weight" :[6]
        }

In [62]:
parameters : [0.1, 4, 200, 1.0, 0, 0.5, 1.5, 6]
accuracy : 0.675
spes     : 0.6744343891402715
sens     : 0.69
auc      : 0.6822171945701357

0.7099095022624434

In [14]:
comb = compute_comb(params)
print(comb[0])
accuracy, specificity, sensitivity, auc = my_cross_val( 10, train_total, test_total, train_total_NoCvd, train_total_Cvd,comb[0])

[0.1, 4, 200, 1.0, 0, 0.5, 1.5, 6]


In [15]:
max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)print(mean(accuracy))
print(mean(specificity))
print(mean(sensitivity))
print(mean(auc))

0.675
0.6744343891402715
0.69
0.6822171945701357


In [10]:
# https://www.geeksforgeeks.org/python-all-possible-permutations-of-n-lists/

def compute_comb(params):
    
    # initializing lists 
    list1 = params.get("learning_rate")
    list2 = params.get("max_depth")
    list3 = params.get("n_estimators") 
    list4 = params.get("min_child_weight")
    list5 = params.get("gamma")    
    list6 = params.get("colsample_bytree")
    list7 = params.get("reg_lambda") 
    list8 = params.get("scale_pos_weight")

#     # printing lists  
#     print ("The original lists are : " + str(list1) +
#                                    " " + str(list2) + 
#                                    " " + str(list3) + 
#                                    " " + str(list4) + 
#                                    " " + str(list5) + 
#                                    " " + str(list6) +
#                                    " " + str(list7) +
#                                    " " + str(list8)) 

    # using list comprehension  
    # to compute all pmax_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)ossible permutations 
    res = [[i, j, k, l, m, n, o, p] for i in list1  
                                    for j in list2 
                                    for k in list3 
                                    for l in list4 
                                    for m in list5 
                                    for n in list6 
                                    for o in list7
                                    for p in list8] 

    # printing result 
#     print ("All possible permutations are : " +  str(res))
    return res

In [11]:
class style:
    BOLD = '\033[1m'
    END = '\033[0m'

In [12]:
# https://towardsdatascience.com/train-test-split-and-cross-validation-in-python-80b61beca4b6

from sklearn.metrics import  confusion_matrix,roc_curve, roc_auc_score, accuracy_score
from imxgboost.imbalance_xgb import imbalance_xgboost as imb_xgb
from sklearn.model_selection import StratifiedKFold # import KFold
from statistics import mean

def gridsearch(params):
    max_sens = 0
    max_spes = 0
    max_acc = 0
    best_params = []
    max_params = []
    max_auc = 0
    combs = compute_comb(params)
    print(len(combs))
    for j in range(len(combs)):
        print(j)
        accuracy, specificity, sensitivity, auc = my_cross_val( 10, train_total, test_total, train_total_NoCvd, train_total_Cvd,combs[j])
        if mean(sensitivity)> 0.5 and mean(specificity)>0.6 and mean(accuracy)>0.6 and mean(auc)>0.5:
            print(style.BOLD + "----------------------------------------------------------------"+ style.END)
            print(combs[j])
            print (style.BOLD + 'accuracy    ' + style.END, mean(accuracy))
            print (style.BOLD + 'specificity ' + style.END, mean(specificity))
            print (style.BOLD + 'sensitivity ' + style.END, mean(sensitivity))
            print (style.BOLD + 'auc         ' + style.END, mean(auc))
            print(style.BOLD + "----------------------------------------------------------------"+ style.END)
        else:
            print(combs[j])
            print("accuracy    ",mean(accuracy))
            print("specificity ",mean(specificity))
            print("sensitivity ",mean(sensitivity))
            print("auc         ",mean(auc))
        best_params.append([combs[j],mean(accuracy),mean(specificity),mean(sensitivity),mean(auc)])
        if mean(auc)> max_auc:
            max_sens = mean(sensitivity)
            max_spes = mean(specificity)
            max_acc = mean(accuracy)
            max_auc = mean(auc)
            max_params = combs[j]
    return max_sens, max_params, max_spes, max_acc, max_auc, best_params

# Ratio = 2

In [17]:
params = {
                    "learning_rate"    :[0.1,0.2, 0.3,0.4],  #0.01-0.2 Makes the model more robust by shrinking the weights on each step
                    "max_depth"        :[1,2, 3,4],  #3-10 control over-fitting as higher depth will allow model to learn relations very specific to a particular sample
                    "n_estimators"     :[100, 200, 300,400],
                    "min_child_weight" :[1,2,3],         #0.5-1 small values might lead to under-fitting
                    "gamma"            :[0, 0.5,1],            #Makes the algorithm conservative --> No overfitting
                    "colsample_bytree" :[0.5,0.75, 1.0], #0.5-1
                     "reg_lambda"      :[1, 1.5, 2], #  it should be explored to reduce overfitting.
                    "scale_pos_weight" :[1,2,3,4,5]
        }

Στην συνέχεια τρέχουμε την gridsearch και εμφανίζουμε όλα τα αποτελέσματα. Μεταξύ γραμμών και με bold τυπώνονται οι τιμές που ικανοπούν τις συνθήκες:
    mean(sensitivity)> 0.5 and mean(specificity)>0.6 and mean(accuracy)>0.6 and mean(auc)>0.5:

In [18]:
max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(parammax_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)s)

25920
0
[0.1, 1, 100, 1, 0, 0.5, 1, 1]
accuracy     0.8857142857142857
specificity  0.9441176470588235
sensitivity  0.145
auc          0.5445588235294118
1
[0.1, 1, 100, 1, 0, 0.5, 1, 2]
accuracy     0.6589285714285714
specificity  0.6783936651583711
sensitivity  0.415
auc          0.5466968325791856
2
[0.1, 1, 100, 1, 0, 0.5, 1, 3]
accuracy     0.46071428571428574
specificity  0.4395550527903469
sensitivity  0.73
auc          0.5847775263951734
3
[0.1, 1, 100, 1, 0, 0.5, 1, 4]
accuracy     0.34285714285714286
specificity  0.3085218702865762
sensitivity  0.78
auc          0.5442609351432881
4
[0.1, 1, 100, 1, 0, 0.5, 1, 5]
accuracy     0.25357142857142856
specificity  0.20822021116138764
sensitivity  0.83
auc          0.5191101055806938
5
[0.1, 1, 100, 1, 0, 0.5, 1.5, 1]
accuracy     0.8857142857142857
specificity  0.9460407239819004
sensitivity  0.125
auc          0.5355203619909502
6
[0.1, 1, 100, 1, 0, 0.5, 1.5, 2]
accuracy     0.6571428571428571
specificity  0.6783559577677225
sens

[0.1, 1, 100, 1, 0.5, 0.5, 2, 1]
accuracy     0.8892857142857143
specificity  0.9499245852187028
sensitivity  0.125
auc          0.5374622926093514
56
[0.1, 1, 100, 1, 0.5, 0.5, 2, 2]
accuracy     0.6571428571428571
specificity  0.6783936651583711
sensitivity  0.39
auc          0.5341968325791855
57
[0.1, 1, 100, 1, 0.5, 0.5, 2, 3]
accuracy     0.46071428571428574
specificity  0.43763197586727
sensitivity  0.755
auc          0.596315987933635
58
[0.1, 1, 100, 1, 0.5, 0.5, 2, 4]
accuracy     0.32321428571428573
specificity  0.28536953242835594
sensitivity  0.805
auc          0.545184766214178
59
[0.1, 1, 100, 1, 0.5, 0.5, 2, 5]
accuracy     0.24821428571428572
specificity  0.20052790346907995
sensitivity  0.855
auc          0.5277639517345399
60
[0.1, 1, 100, 1, 0.5, 0.75, 1, 1]
accuracy     0.8839285714285714
specificity  0.9421945701357466
sensitivity  0.145
auc          0.5435972850678733
61
[0.1, 1, 100, 1, 0.5, 0.75, 1, 2]
accuracy     0.65
specificity  0.6725490196078432
sensitivi

[0.1, 1, 100, 1, 1, 0.75, 1.5, 1]
accuracy     0.9035714285714286
specificity  0.9653092006033183
sensitivity  0.125
auc          0.5451546003016591
111
[0.1, 1, 100, 1, 1, 0.75, 1.5, 2]
accuracy     0.6482142857142856
specificity  0.6687405731523378
sensitivity  0.39
auc          0.5293702865761689
112
[0.1, 1, 100, 1, 1, 0.75, 1.5, 3]
accuracy     0.4714285714285714
specificity  0.4511689291101056
sensitivity  0.735
auc          0.5930844645550528
113
[0.1, 1, 100, 1, 1, 0.75, 1.5, 4]
accuracy     0.33214285714285713
specificity  0.29502262443438915
sensitivity  0.805
auc          0.5500113122171946
114
[0.1, 1, 100, 1, 1, 0.75, 1.5, 5]
accuracy     0.24464285714285713
specificity  0.19664404223227752
sensitivity  0.855
auc          0.5258220211161387
115
[0.1, 1, 100, 1, 1, 0.75, 2, 1]
accuracy     0.9035714285714286
specificity  0.9672322775263952
sensitivity  0.1
auc          0.5336161387631976
116
[0.1, 1, 100, 1, 1, 0.75, 2, 2]
accuracy     0.65
specificity  0.6706259426847662
s

[0.1, 1, 100, 2, 0, 1.0, 1, 2]
accuracy     0.6660714285714285
specificity  0.6880090497737557
sensitivity  0.39
auc          0.5390045248868778
167
[0.1, 1, 100, 2, 0, 1.0, 1, 3]
accuracy     0.475
specificity  0.45690045248868777
sensitivity  0.71
auc          0.583450226244344
168
[0.1, 1, 100, 2, 0, 1.0, 1, 4]
accuracy     0.33214285714285713
specificity  0.2969079939668175
sensitivity  0.78
auc          0.5384539969834088
169
[0.1, 1, 100, 2, 0, 1.0, 1, 5]
accuracy     0.2517857142857143
specificity  0.20452488687782805
sensitivity  0.855
auc          0.529762443438914
170
[0.1, 1, 100, 2, 0, 1.0, 1.5, 1]
accuracy     0.8839285714285714
specificity  0.9441553544494721
sensitivity  0.12
auc          0.532077677224736
171
[0.1, 1, 100, 2, 0, 1.0, 1.5, 2]
accuracy     0.6625
specificity  0.6841251885369533
sensitivity  0.39
auc          0.5370625942684766
172
[0.1, 1, 100, 2, 0, 1.0, 1.5, 3]
accuracy     0.46785714285714286
specificity  0.44913273001508297
sensitivity  0.71
auc      

[0.1, 1, 100, 2, 0.5, 1.0, 2, 2]
accuracy     0.6625
specificity  0.6841628959276018
sensitivity  0.39
auc          0.5370814479638009
222
[0.1, 1, 100, 2, 0.5, 1.0, 2, 3]
accuracy     0.4660714285714286
specificity  0.44720965309200605
sensitivity  0.71
auc          0.578604826546003
223
[0.1, 1, 100, 2, 0.5, 1.0, 2, 4]
accuracy     0.3267857142857143
specificity  0.28925339366515834
sensitivity  0.805
auc          0.5471266968325792
224
[0.1, 1, 100, 2, 0.5, 1.0, 2, 5]
accuracy     0.24285714285714285
specificity  0.19283559577677226
sensitivity  0.88
auc          0.5364177978883862
225
[0.1, 1, 100, 2, 1, 0.5, 1, 1]
accuracy     0.8982142857142857
specificity  0.9614630467571644
sensitivity  0.1
auc          0.5307315233785822
226
[0.1, 1, 100, 2, 1, 0.5, 1, 2]
accuracy     0.6678571428571428
specificity  0.6899321266968326
sensitivity  0.39
auc          0.5399660633484162
227
[0.1, 1, 100, 2, 1, 0.5, 1, 3]
accuracy     0.4625
specificity  0.44532428355957765
sensitivity  0.685
auc 

...

[0.4, 4, 400, 2, 0.5, 0.75, 1, 5]
accuracy     0.725
specificity  0.7496229260935143
sensitivity  0.415
auc          0.5823114630467572
25715
[0.4, 4, 400, 2, 0.5, 0.75, 1.5, 1]
accuracy     0.8303571428571429
specificity  0.8768099547511312
sensitivity  0.24
auc          0.5584049773755656
25716
[0.4, 4, 400, 2, 0.5, 0.75, 1.5, 2]
accuracy     0.7803571428571429
specificity  0.8132730015082956
sensitivity  0.365
auc          0.5891365007541478
25717
[0.4, 4, 400, 2, 0.5, 0.75, 1.5, 3]
accuracy     0.7446428571428572
specificity  0.7671191553544495
sensitivity  0.465
auc          0.6160595776772247
25718
[0.4, 4, 400, 2, 0.5, 0.75, 1.5, 4]
accuracy     0.7321428571428571
specificity  0.7554298642533936
sensitivity  0.44
auc          0.5977149321266968
25719
[0.4, 4, 400, 2, 0.5, 0.75, 1.5, 5]
accuracy     0.7125
specificity  0.732315233785822
sensitivity  0.465
auc          0.598657616892911
25720
[0.4, 4, 400, 2, 0.5, 0.75, 2, 1]
accuracy     0.8232142857142857
specificity  0.86911764

[0.4, 4, 400, 2, 1, 0.75, 1.5, 2]
accuracy     0.7821428571428571
specificity  0.8132730015082956
sensitivity  0.395
auc          0.6041365007541478
25762
[0.4, 4, 400, 2, 1, 0.75, 1.5, 3]
accuracy     0.7392857142857143
specificity  0.7612745098039215
sensitivity  0.465
auc          0.6131372549019608
25763
[0.4, 4, 400, 2, 1, 0.75, 1.5, 4]
accuracy     0.7214285714285714
specificity  0.7439291101055807
sensitivity  0.44
auc          0.5919645550527903
25764
----------------------------------------------------------------
[0.4, 4, 400, 2, 1, 0.75, 1.5, 5]
accuracy     0.7071428571428571
specificity  0.7208521870286576
sensitivity  0.545
auc          0.6329260935143288
----------------------------------------------------------------
25765
[0.4, 4, 400, 2, 1, 0.75, 2, 1]
accuracy     0.8392857142857143
specificity  0.8883107088989441
sensitivity  0.215
auc          0.5516553544494721
25766
[0.4, 4, 400, 2, 1, 0.75, 2, 2]
accuracy     0.7821428571428571
specificity  0.8113499245852187
se

[0.4, 4, 400, 3, 0, 0.75, 1.5, 2]
accuracy     0.7571428571428571
specificity  0.7880844645550528
sensitivity  0.365
auc          0.5765422322775264
25807
[0.4, 4, 400, 3, 0, 0.75, 1.5, 3]
accuracy     0.7517857142857143
specificity  0.7784690799396682
sensitivity  0.415
auc          0.596734539969834
25808
[0.4, 4, 400, 3, 0, 0.75, 1.5, 4]
accuracy     0.7357142857142858
specificity  0.761236802413273
sensitivity  0.415
auc          0.5881184012066365
25809
[0.4, 4, 400, 3, 0, 0.75, 1.5, 5]
accuracy     0.7303571428571428
specificity  0.7535444947209653
sensitivity  0.44
auc          0.5967722473604826
25810
[0.4, 4, 400, 3, 0, 0.75, 2, 1]
accuracy     0.8017857142857143
specificity  0.8440422322775264
sensitivity  0.265
auc          0.5545211161387632
25811
[0.4, 4, 400, 3, 0, 0.75, 2, 2]
accuracy     0.7696428571428571
specificity  0.8017345399698341
sensitivity  0.365
auc          0.5833672699849171
25812
[0.4, 4, 400, 3, 0, 0.75, 2, 3]
accuracy     0.7553571428571428
specificity  

[0.4, 4, 400, 3, 0.5, 0.75, 2, 3]
accuracy     0.7535714285714286
specificity  0.7806184012066365
sensitivity  0.415
auc          0.5978092006033182
25858
[0.4, 4, 400, 3, 0.5, 0.75, 2, 4]
accuracy     0.7232142857142857
specificity  0.7420437405731524
sensitivity  0.49
auc          0.6160218702865762
25859
[0.4, 4, 400, 3, 0.5, 0.75, 2, 5]
accuracy     0.7267857142857143
specificity  0.7458144796380091
sensitivity  0.49
auc          0.6179072398190045
25860
[0.4, 4, 400, 3, 0.5, 1.0, 1, 1]
accuracy     0.8232142857142857
specificity  0.871078431372549
sensitivity  0.22
auc          0.5455392156862745
25861
[0.4, 4, 400, 3, 0.5, 1.0, 1, 2]
accuracy     0.7928571428571428
specificity  0.8228506787330316
sensitivity  0.415
auc          0.6189253393665158
25862
[0.4, 4, 400, 3, 0.5, 1.0, 1, 3]
accuracy     0.7446428571428572
specificity  0.7651583710407239
sensitivity  0.49
auc          0.627579185520362
25863
----------------------------------------------------------------
[0.4, 4, 400, 

[0.4, 4, 400, 3, 1, 0.75, 2, 2]
accuracy     0.7839285714285714
specificity  0.8152337858220211
sensitivity  0.39
auc          0.6026168929110106
25902
----------------------------------------------------------------
[0.4, 4, 400, 3, 1, 0.75, 2, 3]
accuracy     0.7392857142857143
specificity  0.7555052790346908
sensitivity  0.54
auc          0.6477526395173454
----------------------------------------------------------------
25903
[0.4, 4, 400, 3, 1, 0.75, 2, 4]
accuracy     0.6928571428571428
specificity  0.7093137254901961
sensitivity  0.49
auc          0.599656862745098
25904
[0.4, 4, 400, 3, 1, 0.75, 2, 5]
accuracy     0.7
specificity  0.718815987933635
sensitivity  0.465
auc          0.5919079939668175
25905
[0.4, 4, 400, 3, 1, 1.0, 1, 1]
accuracy     0.8446428571428571
specificity  0.8960784313725491
sensitivity  0.195
auc          0.5455392156862745
25906
[0.4, 4, 400, 3, 1, 1.0, 1, 2]
accuracy     0.7892857142857143
specificity  0.8210030165912519
sensitivity  0.39
auc          

In [20]:
print(max_params)
print(max_acc)
print(max_spes)
print(max_sens)
print(max_auc)

[0.2, 3, 100, 1, 0.5, 1.0, 2, 4]
0.7285714285714285
0.7360859728506787
0.64
0.6880429864253393


In [21]:
#Τυπώνονται περιπτώσεις που accuracy>0.6 και specificity>0.6 και sensitivity>0.6 και auc>0.6
s = 0
for i in range(len(best_params)):
    if best_params[i][4] > 0.68 :
        print("parameters :",best_params[i][0])
        print("accuracy :",best_params[i][1])
        print("spes     :",best_params[i][2])
        print("sens     :",best_params[i][3])
        print("auc      :",best_params[i][4])
        print("------------------------------------------------")
        s+=1
print(s)

parameters : [0.2, 3, 100, 1, 0.5, 1.0, 2, 4]
accuracy : 0.7285714285714285
spes     : 0.7360859728506787
sens     : 0.64
auc      : 0.6880429864253393
------------------------------------------------
parameters : [0.2, 3, 200, 1, 0.5, 1.0, 2, 4]
accuracy : 0.7285714285714285
spes     : 0.7360859728506787
sens     : 0.64
auc      : 0.6880429864253393
------------------------------------------------
parameters : [0.2, 3, 300, 1, 0.5, 1.0, 2, 4]
accuracy : 0.7285714285714285
spes     : 0.7360859728506787
sens     : 0.64
auc      : 0.6880429864253393
------------------------------------------------
parameters : [0.2, 3, 400, 1, 0.5, 1.0, 2, 4]
accuracy : 0.7285714285714285
spes     : 0.7360859728506787
sens     : 0.64
auc      : 0.6880429864253393
------------------------------------------------
parameters : [0.3, 3, 300, 3, 0, 1.0, 1, 5]
accuracy : 0.7446428571428572
spes     : 0.7554298642533936
sens     : 0.615
auc      : 0.6852149321266968
---------------------------------------------

In [22]:
params = {
                    "learning_rate"    :[0.1,0.2, 0.3,0.4],  #0.01-0.2 Makes the model more robust by shrinking the weights on each step
                    "max_depth"        :[1,2, 3,4],  #3-10 control over-fitting as higher depth will allow model to learn relations very specific to a particular sample
                    "n_estimators"     :[100, 200, 300,400],
                    "min_child_weight" :[4],         #0.5-1 small values might lead to under-fitting
                    "gamma"            :[0, 0.5,1],            #Makes the algorithm conservative --> No overfitting
                    "colsample_bytree" :[0.5,0.75, 1.0], #0.5-1
                     "reg_lambda"      :[1, 1.5, 2], #  it should be explored to reduce overfitting.
                    "scale_pos_weight" :[1,2,3,4,5]
        }

In [23]:
max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)

8640
0
[0.1, 1, 100, 4, 0, 0.5, 1, 1]
accuracy     0.8839285714285714
specificity  0.9384238310708899
sensitivity  0.195
auc          0.566711915535445
1
[0.1, 1, 100, 4, 0, 0.5, 1, 2]
accuracy     0.6607142857142857
specificity  0.680316742081448
sensitivity  0.415
auc          0.547658371040724
2
[0.1, 1, 100, 4, 0, 0.5, 1, 3]
accuracy     0.4714285714285714
specificity  0.45301659125188537
sensitivity  0.705
auc          0.5790082956259427
3
[0.1, 1, 100, 4, 0, 0.5, 1, 4]
accuracy     0.3357142857142857
specificity  0.2988310708898944
sensitivity  0.805
auc          0.5519155354449472
4
[0.1, 1, 100, 4, 0, 0.5, 1, 5]
accuracy     0.25892857142857145
specificity  0.21406485671191552
sensitivity  0.83
auc          0.5220324283559578
5
[0.1, 1, 100, 4, 0, 0.5, 1.5, 1]
accuracy     0.8839285714285714
specificity  0.9384238310708899
sensitivity  0.195
auc          0.566711915535445
6
[0.1, 1, 100, 4, 0, 0.5, 1.5, 2]
accuracy     0.6607142857142857
specificity  0.680316742081448
sensitivi

[0.1, 1, 100, 4, 0.5, 0.5, 2, 1]
accuracy     0.8946428571428572
specificity  0.9518853695324283
sensitivity  0.175
auc          0.5634426847662142
56
[0.1, 1, 100, 4, 0.5, 0.5, 2, 2]
accuracy     0.6589285714285714
specificity  0.6783936651583711
sensitivity  0.415
auc          0.5466968325791856
57
[0.1, 1, 100, 4, 0.5, 0.5, 2, 3]
accuracy     0.4571428571428572
specificity  0.43755656108597285
sensitivity  0.705
auc          0.5712782805429865
58
[0.1, 1, 100, 4, 0.5, 0.5, 2, 4]
accuracy     0.32857142857142857
specificity  0.2911010558069382
sensitivity  0.805
auc          0.5480505279034691
59
[0.1, 1, 100, 4, 0.5, 0.5, 2, 5]
accuracy     0.24285714285714285
specificity  0.19671945701357466
sensitivity  0.83
auc          0.5133597285067873
60
[0.1, 1, 100, 4, 0.5, 0.75, 1, 1]
accuracy     0.8839285714285714
specificity  0.9384238310708899
sensitivity  0.195
auc          0.566711915535445
61
[0.1, 1, 100, 4, 0.5, 0.75, 1, 2]
accuracy     0.6517857142857143
specificity  0.6707013574

[0.1, 1, 100, 4, 1, 0.75, 1.5, 1]
accuracy     0.9107142857142857
specificity  0.9749622926093514
sensitivity  0.1
auc          0.5374811463046757
111
[0.1, 1, 100, 4, 1, 0.75, 1.5, 2]
accuracy     0.6571428571428571
specificity  0.6745475113122172
sensitivity  0.44
auc          0.5572737556561086
112
[0.1, 1, 100, 4, 1, 0.75, 1.5, 3]
accuracy     0.4625
specificity  0.4414027149321267
sensitivity  0.73
auc          0.5857013574660633
113
[0.1, 1, 100, 4, 1, 0.75, 1.5, 4]
accuracy     0.3267857142857143
specificity  0.2891779788838612
sensitivity  0.805
auc          0.5470889894419306
114
[0.1, 1, 100, 4, 1, 0.75, 1.5, 5]
accuracy     0.24821428571428572
specificity  0.20060331825037708
sensitivity  0.855
auc          0.5278016591251885
115
[0.1, 1, 100, 4, 1, 0.75, 2, 1]
accuracy     0.9107142857142857
specificity  0.9749622926093514
sensitivity  0.1
auc          0.5374811463046757
116
[0.1, 1, 100, 4, 1, 0.75, 2, 2]
accuracy     0.6571428571428571
specificity  0.6745475113122171
sens

[0.1, 1, 200, 4, 0, 1.0, 1, 1]
accuracy     0.8535714285714285
specificity  0.9017722473604827
sensitivity  0.245
auc          0.5733861236802413
166
[0.1, 1, 200, 4, 0, 1.0, 1, 2]
accuracy     0.6821428571428572
specificity  0.7015082956259426
sensitivity  0.44
auc          0.5707541478129713
167
[0.1, 1, 200, 4, 0, 1.0, 1, 3]
accuracy     0.5196428571428572
specificity  0.5108220211161387
sensitivity  0.64
auc          0.5754110105580694
168
[0.1, 1, 200, 4, 0, 1.0, 1, 4]
accuracy     0.4160714285714286
specificity  0.3894419306184012
sensitivity  0.76
auc          0.5747209653092006
169
[0.1, 1, 200, 4, 0, 1.0, 1, 5]
accuracy     0.3482142857142857
specificity  0.30844645550527905
sensitivity  0.855
auc          0.5817232277526395
170
[0.1, 1, 200, 4, 0, 1.0, 1.5, 1]
accuracy     0.8535714285714285
specificity  0.9017722473604827
sensitivity  0.245
auc          0.5733861236802413
171
[0.1, 1, 200, 4, 0, 1.0, 1.5, 2]
accuracy     0.6732142857142858
specificity  0.6918552036199095
sen

[0.1, 1, 200, 4, 0.5, 1.0, 2, 1]
accuracy     0.8821428571428571
specificity  0.9364253393665158
sensitivity  0.195
auc          0.565712669683258
221
[0.1, 1, 200, 4, 0.5, 1.0, 2, 2]
accuracy     0.6785714285714286
specificity  0.6976244343891402
sensitivity  0.44
auc          0.5688122171945701
222
[0.1, 1, 200, 4, 0.5, 1.0, 2, 3]
accuracy     0.5089285714285714
specificity  0.4992081447963801
sensitivity  0.64
auc          0.56960407239819
223
[0.1, 1, 200, 4, 0.5, 1.0, 2, 4]
accuracy     0.40535714285714286
specificity  0.3759049773755656
sensitivity  0.785
auc          0.5804524886877828
224
[0.1, 1, 200, 4, 0.5, 1.0, 2, 5]
accuracy     0.3410714285714286
specificity  0.30071644042232276
sensitivity  0.855
auc          0.5778582202111614
225
[0.1, 1, 200, 4, 1, 0.5, 1, 1]
accuracy     0.9089285714285714
specificity  0.9730392156862745
sensitivity  0.1
auc          0.5365196078431372
226
[0.1, 1, 200, 4, 1, 0.5, 1, 2]
accuracy     0.6553571428571429
specificity  0.6745098039215687


...

----------------------------------------------------------------
[0.4, 4, 300, 4, 1, 0.5, 1, 5]
accuracy     0.6875
specificity  0.6976621417797888
sensitivity  0.565
auc          0.6313310708898944
----------------------------------------------------------------
8465
[0.4, 4, 300, 4, 1, 0.5, 1.5, 1]
accuracy     0.8446428571428571
specificity  0.894079939668175
sensitivity  0.22
auc          0.5570399698340874
8466
[0.4, 4, 300, 4, 1, 0.5, 1.5, 2]
accuracy     0.7803571428571429
specificity  0.8075414781297134
sensitivity  0.44
auc          0.6237707390648567
8467
----------------------------------------------------------------
[0.4, 4, 300, 4, 1, 0.5, 1.5, 3]
accuracy     0.7410714285714286
specificity  0.759313725490196
sensitivity  0.515
auc          0.637156862745098
----------------------------------------------------------------
8468
----------------------------------------------------------------
[0.4, 4, 300, 4, 1, 0.5, 1.5, 4]
accuracy     0.7053571428571429
specificity  0.72

----------------------------------------------------------------
[0.4, 4, 300, 4, 1, 1.0, 1.5, 5]
accuracy     0.6625
specificity  0.670739064856712
sensitivity  0.565
auc          0.617869532428356
----------------------------------------------------------------
8500
[0.4, 4, 300, 4, 1, 1.0, 2, 1]
accuracy     0.8642857142857143
specificity  0.919155354449472
sensitivity  0.175
auc          0.547077677224736
8501
[0.4, 4, 300, 4, 1, 1.0, 2, 2]
accuracy     0.75
specificity  0.7785822021116139
sensitivity  0.39
auc          0.584291101055807
8502
----------------------------------------------------------------
[0.4, 4, 300, 4, 1, 1.0, 2, 3]
accuracy     0.7053571428571429
specificity  0.7189668174962293
sensitivity  0.54
auc          0.6294834087481146
----------------------------------------------------------------
8503
----------------------------------------------------------------
[0.4, 4, 300, 4, 1, 1.0, 2, 4]
accuracy     0.6732142857142858
specificity  0.6783559577677225
sensiti

[0.4, 4, 400, 4, 0, 1.0, 2, 4]
accuracy     0.7375
specificity  0.7594268476621417
sensitivity  0.465
auc          0.6122134238310708
8549
[0.4, 4, 400, 4, 0, 1.0, 2, 5]
accuracy     0.7232142857142857
specificity  0.7439668174962293
sensitivity  0.465
auc          0.6044834087481146
8550
[0.4, 4, 400, 4, 0.5, 0.5, 1, 1]
accuracy     0.8214285714285714
specificity  0.8691176470588236
sensitivity  0.22
auc          0.5445588235294118
8551
[0.4, 4, 400, 4, 0.5, 0.5, 1, 2]
accuracy     0.7732142857142857
specificity  0.8055429864253394
sensitivity  0.365
auc          0.5852714932126697
8552
[0.4, 4, 400, 4, 0.5, 0.5, 1, 3]
accuracy     0.7392857142857143
specificity  0.7631975867269984
sensitivity  0.44
auc          0.6015987933634992
8553
[0.4, 4, 400, 4, 0.5, 0.5, 1, 4]
accuracy     0.7125
specificity  0.7303921568627451
sensitivity  0.49
auc          0.6101960784313726
8554
----------------------------------------------------------------
[0.4, 4, 400, 4, 0.5, 0.5, 1, 5]
accuracy     0.

[0.4, 4, 400, 4, 0.5, 1.0, 1.5, 2]
accuracy     0.7785714285714286
specificity  0.8094268476621418
sensitivity  0.39
auc          0.5997134238310708
8587
[0.4, 4, 400, 4, 0.5, 1.0, 1.5, 3]
accuracy     0.7375
specificity  0.7592760180995475
sensitivity  0.465
auc          0.6121380090497738
8588
----------------------------------------------------------------
[0.4, 4, 400, 4, 0.5, 1.0, 1.5, 4]
accuracy     0.7142857142857143
specificity  0.7305052790346908
sensitivity  0.515
auc          0.6227526395173454
----------------------------------------------------------------
8589
----------------------------------------------------------------
[0.4, 4, 400, 4, 0.5, 1.0, 1.5, 5]
accuracy     0.6803571428571429
specificity  0.6881221719457014
sensitivity  0.59
auc          0.6390610859728507
----------------------------------------------------------------
8590
[0.4, 4, 400, 4, 0.5, 1.0, 2, 1]
accuracy     0.85
specificity  0.898001508295626
sensitivity  0.24
auc          0.5690007541478129
85

----------------------------------------------------------------
[0.4, 4, 400, 4, 1, 0.75, 2, 4]
accuracy     0.6803571428571429
specificity  0.6899321266968326
sensitivity  0.565
auc          0.6274660633484163
----------------------------------------------------------------
8624
----------------------------------------------------------------
[0.4, 4, 400, 4, 1, 0.75, 2, 5]
accuracy     0.6803571428571429
specificity  0.6898567119155354
sensitivity  0.565
auc          0.6274283559577677
----------------------------------------------------------------
8625
[0.4, 4, 400, 4, 1, 1.0, 1, 1]
accuracy     0.8446428571428571
specificity  0.8999245852187029
sensitivity  0.15
auc          0.5249622926093515
8626
[0.4, 4, 400, 4, 1, 1.0, 1, 2]
accuracy     0.7553571428571428
specificity  0.7863122171945701
sensitivity  0.365
auc          0.575656108597285
8627
[0.4, 4, 400, 4, 1, 1.0, 1, 3]
accuracy     0.7053571428571429
specificity  0.7245852187028657
sensitivity  0.465
auc          0.5947926

In [24]:
print(max_params)
print(max_acc)
print(max_spes)
print(max_sens)
print(max_auc)

[0.1, 3, 100, 4, 1, 0.75, 1.5, 3]
0.6910714285714286
0.6938914027149321
0.66
0.676945701357466


In [25]:
#Τυπώνονται περιπτώσεις που accuracy>0.6 και specificity>0.6 και sensitivity>0.6 και auc>0.6
s = 0
for i in range(len(best_params)):
    if best_params[i][4] > 0.675 :
        print("parameters :",best_params[i][0])
        print("accuracy :",best_params[i][1])
        print("spes     :",best_params[i][2])
        print("sens     :",best_params[i][3])
        print("auc      :",best_params[i][4])
        print("------------------------------------------------")
        s+=1
print(s)

parameters : [0.1, 3, 100, 4, 0, 1.0, 1, 3]
accuracy : 0.7071428571428572
spes     : 0.7130844645550528
sens     : 0.64
auc      : 0.6765422322775264
------------------------------------------------
parameters : [0.1, 3, 100, 4, 1, 0.75, 1.5, 3]
accuracy : 0.6910714285714286
spes     : 0.6938914027149321
sens     : 0.66
auc      : 0.676945701357466
------------------------------------------------
parameters : [0.1, 4, 200, 4, 0.5, 1.0, 2, 4]
accuracy : 0.7071428571428572
spes     : 0.7130844645550528
sens     : 0.64
auc      : 0.6765422322775264
------------------------------------------------
parameters : [0.1, 4, 300, 4, 0.5, 1.0, 2, 4]
accuracy : 0.7071428571428572
spes     : 0.7130844645550528
sens     : 0.64
auc      : 0.6765422322775264
------------------------------------------------
parameters : [0.1, 4, 400, 4, 0.5, 1.0, 2, 4]
accuracy : 0.7071428571428572
spes     : 0.7130844645550528
sens     : 0.64
auc      : 0.6765422322775264
----------------------------------------------